In [1]:
import pickle
import os
import sys
import json
from moralstrength.moralstrength import string_moral_values
parent_directory = os.path.abspath(os.path.join(os.getcwd(), '..', '..'))
sys.path.append(parent_directory)
from project.utils.classes.tokenizer import Tokenizer
import warnings
warnings.filterwarnings("ignore")
import numpy as np
import gensim.downloader as api
word_vectors = api.load("glove-twitter-200")

#### Read in the Reddit Data

In [ ]:
parent_directory = os.path.abspath(os.path.join(os.getcwd(), '..'))

pickle_file_path_comment = os.path.join(parent_directory,
    'data_collection/project_data/climateCommentsDf.pickle')

pickle_file_path_submission = os.path.join(parent_directory,
    'data_collection/project_data/climateSubmissionsDf.pickle')

with open(pickle_file_path_comment, 'rb') as f:
    comments_df = pickle.load(f)

with open(pickle_file_path_submission, 'rb') as f:
    submission_df = pickle.load(f)

In [3]:
#comments_df.head()
comments_df = comments_df[~comments_df['body'].isin(['[removed]', '[deleted]'])]
comments_df['subreddit'].unique()
#subset_comments_df = comments_df.iloc[0:10000]
#subset_comments_df = comments_df
#subset_comments_df.head()

id  subreddit                         body                author  \
1  inlw0wi  worldnews              Needed a laugh!  serious-activity-228   
3  inlxwat  worldnews                       Asked!           dieyoufool3   
6  inget84  worldnews  Soviet planes do not crash.  of_a_varsity_athlete   
8  inm3jkr  worldnews   I thought he was in London             henrycolp   
9  inm5tt7  worldnews         Lol you were saying?        quite_largeboi   

   score  gilded  created_utc parent_id link_id  retrieved_on  \
1      3       0   1662654781   inlvhve  x8yhv5    1665086761   
3      3       0   1662655481   inlszmb  x94ag0    1665086696   
6      1       0   1662561420    x80hyn  x80hyn    1665093621   
8      3       0   1662657593   inm32gu  x8yhv5    1665086500   
9      5       0   1662658442   inlmp4c  x8yhv5    1665086420   

   controversiality  is_submitter  
1                 0         False  
3                 0          True  
6                 0         False  
8                 0         False  
9                 0         False

In [4]:
#comments_df.to_csv("comments.csv")
subset_comments_df.to_csv("comments.csv")

In [5]:

tokenizer = Tokenizer(filepath='comments.csv',
                      filename='tokenized_comments.csv')
tokenizer.process(cols_to_tokenize=[('body', 'tokenized_body')])

TypeError: 'float' object is not subscriptable

In [ ]:
tokenizer.tokenized_df

Unnamed: 0       id  subreddit  \
0              1  inlw0wi  worldnews   
1              3  inlxwat  worldnews   
2              6  inget84  worldnews   
3              8  inm3jkr  worldnews   
4              9  inm5tt7  worldnews   
...          ...      ...        ...   
9995       12270  iqkzpaq    science   
9996       12271  iqkzpb8   politics   
9997       12272  iqkzpd3   politics   
9998       12273  iqkzpej   politics   
9999       12274  iqkzpgf  worldnews   

                                                   body                author  \
0                                       Needed a laugh!  serious-activity-228   
1                                                Asked!           dieyoufool3   
2                           Soviet planes do not crash.  of_a_varsity_athlete   
3                            I thought he was in London             henrycolp   
4                                  Lol you were saying?        quite_largeboi   
...                                                 ...                   ...   
9995  Speaking of spurious correlations, this rock i...       northraleighguy   
9996  I feel like a moron for not seeing a racial co...          theintrepid1   
9997                        Such a bold prediction too!  karmaisevillikemoney   
9998  Texas could find a way to sue them. But I don'...          vineyardmike   
9999  We were in the process of opening travel to Cu...           jewelbird10   

      score  gilded  created_utc parent_id link_id  retrieved_on  \
0         3       0   1662654781   inlvhve  x8yhv5    1665086761   
1         3       0   1662655481   inlszmb  x94ag0    1665086696   
2         1       0   1662561420    x80hyn  x80hyn    1665093621   
3         3       0   1662657593   inm32gu  x8yhv5    1665086500   
4         5       0   1662658442   inlmp4c  x8yhv5    1665086420   
...     ...     ...          ...       ...     ...           ...   
9995      2       0   1664593810    xrxb0k  xrxb0k    1664959888   
9996     25       0   1664593810   iqktehn  xsipuv    1664959888   
9997      1       0   1664593811   iqkbd5s  xsfyrh    1664959888   
9998      1       0   1664593812   iqkyxu1  xs34mm    1664959888   
9999     -3       0   1664593813    xsjhp2  xsjhp2    1664959888   

      controversiality  is_submitter  \
0                    0         False   
1                    0          True   
2                    0         False   
3                    0         False   
4                    0         False   
...                ...           ...   
9995                 0         False   
9996                 0         False   
9997                 0         False   
9998                 0         False   
9999                 1         False   

                                   tokenized_body_sents  \
0                                     [needed a laugh!]   
1                                              [asked!]   
2                         [soviet planes do not crash.]   
3                          [i thought he was in london]   
4                                [lol you were saying?]   
...                                                 ...   
9995  [speaking of spurious correlations, this rock ...   
9996  [i feel like a moron for not seeing a racial c...   
9997                      [such a bold prediction too!]   
9998  [texas could find a way to sue them., but i do...   
9999  [we were in the process of opening travel to c...   

                                   tokenized_body_words  \
0                                       [needed, laugh]   
1                                               [asked]   
2                               [soviet, planes, crash]   
3                                     [thought, london]   
4                                         [lol, saying]   
...                                                 ...   
9995  [speaking, spurious, correlations, rock, pocke...   
9996  [feel, like, moron, seeing, racial, connected,...   
9997          

#### Method 2: Using moralstrength package

In [ ]:
with open('expanded_moral_foundations_dictionary.json', 'r') as f:
    word_to_moral_foundation_expanded = json.load(f)

def compute_similarity(comment, foundation_words):
    similarities = []
    for word in comment:  # word in reddit comment
        if word in word_vectors:  # check for presence in embeddings
            word_vec = word_vectors[word]  # get the embedding
            for foundation_word in foundation_words:  # loop through moral foundation words
                if foundation_word in word_vectors:  # check for presence in embeddings
                    foundation_word_vec = word_vectors[foundation_word]  # get the embedding
                    sim = np.dot(word_vec, foundation_word_vec) / (np.linalg.norm(word_vec) * np.linalg.norm(foundation_word_vec))
                    similarities.append(sim)
                    
    # Aggregate similarities instead of selecting the maximum
    if similarities:
        return np.mean(similarities)  # Or consider other aggregation methods like sum
    else:
        return 0

def classify_sentence_with_profile(sentence, moral_foundations_dict):
    foundation_scores = {}
    
    for foundation, words in moral_foundations_dict.items():
        foundation_scores[foundation] = compute_similarity(sentence, words)
    
    # Normalize scores to sum to 1 for a probability-like interpretation
    #total_score = sum(foundation_scores.values())
    #if total_score > 0:
        #for foundation in foundation_scores:
            #foundation_scores[foundation] /= total_score
    
    return foundation_scores

In [ ]:
comments = tokenizer.tokenized_df['tokenized_body_words_norm']
for comment in comments:
    try:
        if comment[0] not in ['remove', 'delete']:
            classification_profile = classify_sentence_with_profile(comment, word_to_moral_foundation_expanded)
            print(f"Similarity profile for {comment} across moral foundations: {classification_profile}")
    except:
        pass

Similarity profile for ['need', 'laugh'] across moral foundations: {'HarmVirtue': 0.27092072, 'AuthorityVirtue': 0.3317137, 'PurityVirtue': 0.1961919, 'HarmVice': 0.29069972, 'PurityVice': 0.23123395, 'IngroupVice': 0.07064861, 'FairnessVirtue': 0.28741086, 'MoralityGeneral': 0.56136847, 'FairnessVice': 0.12578559, 'IngroupVirtue': 0.31480396, 'AuthorityVice': 0.11954024}
Similarity profile for ['ask'] across moral foundations: {'HarmVirtue': 0.19348916, 'AuthorityVirtue': 0.29293743, 'PurityVirtue': 0.12767164, 'HarmVice': 0.19057558, 'PurityVice': 0.15137106, 'IngroupVice': 0.053664416, 'FairnessVirtue': 0.22479436, 'MoralityGeneral': 0.46031085, 'FairnessVice': 0.096292466, 'IngroupVirtue': 0.25309798, 'AuthorityVice': 0.084531}
Similarity profile for ['soviet', 'plane', 'crash'] across moral foundations: {'HarmVirtue': 0.15329583, 'AuthorityVirtue': 0.19601858, 'PurityVirtue': 0.11836706, 'HarmVice': 0.2066645, 'PurityVice': 0.118800856, 'IngroupVice': 0.11283203, 'FairnessVirtue':

In [ ]:
test_str = ' '
for word in test:
    test_str += ' ' + word
print(test_str)

result = string_moral_values(test_str, model='unigram+freq')
print(result)

  a m i t y
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}


In [ ]:
texts = tokenizer.tokenized_df['tokenized_body_sents']

for text in texts:
    text = text
    print(text)
    #result = estimate_morals(text, process=True)
    result = string_moral_values(text[0], model='unigram+freq')
    print(result)

['needed a laugh!']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['asked!']
{'care': 0.02208495580855399, 'fairness': 0.027164068483193603, 'loyalty': 0.012337675346414789, 'authority': 0.014527929414220054, 'purity': 0.015802333579890755, 'non-moral': 0.6395208282683185}
['soviet planes do not crash.']
{'care': 0.45710977866231184, 'fairness': 0.40053123501041876, 'loyalty': 0.04458018795655627, 'authority': 0.3684710379078417, 'purity': 0.12571725952988658, 'non-moral': 0.06315545172225111}
['i thought he was in london']
{'care': 0.07231742266811518, 'fairness': 0.04748130387790942, 'loyalty': 0.04344969593221794, 'authority': 0.028501746693417283, 'purity': 0.07105573460603648, 'non-moral': 0.6514207101165549}
['lol you were saying?']
{'care': 0.039491987582384834, 'fairness': 0.08097898136980541, 'loyalty': 0.02633971662167872, 'aut